<center> <img src = 'd:/KIPI/KIPI.jpg'> </center>

In [24]:
# 패키지 설치하기
!pip install xgboost

   ---------------------------------------- 0.0/124.9 MB ? eta -:--:--
   ---------------------------------------- 1.0/124.9 MB 7.1 MB/s eta 0:00:18
    --------------------------------------- 2.9/124.9 MB 8.4 MB/s eta 0:00:15
   - -------------------------------------- 5.0/124.9 MB 9.1 MB/s eta 0:00:14
   -- ------------------------------------- 6.8/124.9 MB 8.9 MB/s eta 0:00:14
   -- ------------------------------------- 8.9/124.9 MB 9.2 MB/s eta 0:00:13
   --- ------------------------------------ 11.0/124.9 MB 9.4 MB/s eta 0:00:13
   ---- ----------------------------------- 13.6/124.9 MB 9.8 MB/s eta 0:00:12
   ----- ---------------------------------- 16.0/124.9 MB 10.0 MB/s eta 0:00:11
   ----- ---------------------------------- 17.3/124.9 MB 9.6 MB/s eta 0:00:12
   ------ --------------------------------- 19.1/124.9 MB 9.4 MB/s eta 0:00:12
   ------ --------------------------------- 21.5/124.9 MB 9.7 MB/s eta 0:00:11
   ------- -------------------------------- 23.9/124.9 MB 9.9 MB

In [28]:
# 패키지 로딩하기
import pandas as pd
import numpy  as np

from sklearn.model_selection import train_test_split
from sklearn.linear_model    import LinearRegression, Lasso, Ridge, ElasticNet, LogisticRegression
from sklearn.metrics         import mean_squared_error, accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.preprocessing   import MinMaxScaler, StandardScaler
from sklearn.tree            import DecisionTreeClassifier
from sklearn.ensemble        import RandomForestClassifier
from xgboost                 import XGBClassifier

### I. 예측(Prediction)

In [2]:
# 데이터 읽어오기 : housing.csv
file_path = "d:/KIPI/housing.csv"
housing   = pd.read_csv(file_path)
housing.head()

crime    zu  indus  chas    nox     rm   age     dis  rad    tax  pratio  \
0  0.00632  18.0   2.31   0.0  0.538  6.575  65.2  4.0900    1  296.0    15.3   
1  0.02731   0.0   7.07   0.0  0.469  6.421  78.9  4.9671    2  242.0    17.8   
2  0.02729   0.0   7.07   0.0  0.469  7.185  61.1  4.9671    2  242.0    17.8   
3  0.03237   0.0   2.18   0.0  0.458  6.998  45.8  6.0622    3  222.0    18.7   
4  0.06905   0.0   2.18   0.0  0.458  7.147  54.2  6.0622    3  222.0    18.7   

       bk  lstat  medv  
0  396.90   4.98  24.0  
1  396.90   9.14  21.6  
2  392.83   4.03  34.7  
3  394.63   2.94  33.4  
4  396.90   5.33  36.2

In [3]:
# 데이터의 정보 보기
housing.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 506 entries, 0 to 505
Data columns (total 14 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   crime   506 non-null    float64
 1   zu      506 non-null    float64
 2   indus   506 non-null    float64
 3   chas    506 non-null    float64
 4   nox     506 non-null    float64
 5   rm      506 non-null    float64
 6   age     506 non-null    float64
 7   dis     506 non-null    float64
 8   rad     506 non-null    int64  
 9   tax     506 non-null    float64
 10  pratio  506 non-null    float64
 11  bk      506 non-null    float64
 12  lstat   506 non-null    float64
 13  medv    452 non-null    float64
dtypes: float64(13), int64(1)
memory usage: 55.5 KB


In [4]:
# 데이터 전처리(Data Pre-processing) : 결측치 제거(행기준)
housing = housing.dropna(axis = 0)
housing.info()

# 참고
# axis = 0 : 행
# axis = 1 : 열

<class 'pandas.core.frame.DataFrame'>
Index: 452 entries, 0 to 505
Data columns (total 14 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   crime   452 non-null    float64
 1   zu      452 non-null    float64
 2   indus   452 non-null    float64
 3   chas    452 non-null    float64
 4   nox     452 non-null    float64
 5   rm      452 non-null    float64
 6   age     452 non-null    float64
 7   dis     452 non-null    float64
 8   rad     452 non-null    int64  
 9   tax     452 non-null    float64
 10  pratio  452 non-null    float64
 11  bk      452 non-null    float64
 12  lstat   452 non-null    float64
 13  medv    452 non-null    float64
dtypes: float64(13), int64(1)
memory usage: 53.0 KB


In [5]:
# y : medv : 수치형 데이터
# X : y를 제외한 모든 열 : 수치형 데이터

In [8]:
# 데이터 분할하기 : 훈련 데이터 70%, 평가 데이터 30%
y = housing["medv"]
X = housing.drop(columns = ["medv"])  # "medv"를 제외한 모든 열

X_train, X_test, y_train, y_test = train_test_split(
    X, 
    y, 
    test_size    = 0.3,  # 평가 데이터의 비율(30%)
    random_state = 42    # 재현 가능성(Reproducibility)을 위한 난수 고정
)

print("훈련용 데이터 크기 :", X_train.shape, y_train.shape)
print("평가용 데이터 크기 :", X_test.shape,  y_test.shape)

훈련용 데이터 크기 : (316, 13) (316,)
평가용 데이터 크기 : (136, 13) (136,)


In [10]:
# 예측 모형 : Linear Regression, LASSO, Ridge, ElasticNet
# 1단계 : 모형 구축(생성)
# 2단계 : 훈련 데이터를 이용해서 학습(훈련)
# 3단계 : 평가 데이터로 예측
# 4단계 : 모형 성능 평가 : MSE(Mean Square Error), RMSE(Root Mean Square Error)

models = {
    "LinearRegression" : LinearRegression(),
    "Lasso"            : Lasso(),         # 기본 alpha = 1.0
    "Ridge"            : Ridge(),         # 기본 alpha = 1.0
    "ElasticNet"       : ElasticNet()     # 기본 alpha = 1.0, l1_ratio = 0.5
}

for name, model in models.items():
    # (1) 훈련
    model.fit(X_train, y_train)
    
    # (2) 예측
    y_pred = model.predict(X_test)
    
    # (3) 평가 (RMSE)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    print(f"{name} RMSE : {rmse:.4f}")

LinearRegression RMSE : 4.3310
Lasso RMSE : 4.4705
Ridge RMSE : 4.3154
ElasticNet RMSE : 4.5460


In [11]:
# 데이터 변환(Transformation) : Min-Max Normalization, Standardization
# (1) Min-Max Normalization : Min-Max 정규화 : (X - Min) / (Max - Min) : 0 ~ 1
# (2) Standardization       : 표준화         : (X - Mean) / SD         : -3 ~ +3

In [13]:
# (1) Min-Max Normalization : Min-Max 정규화 : (X - Min) / (Max - Min) : 0 ~ 1
scaler         = MinMaxScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled  = scaler.transform(X_test)

models = {
    "LinearRegression" : LinearRegression(),
    "Lasso"            : Lasso(),           
    "Ridge"            : Ridge(),           
    "ElasticNet"       : ElasticNet()  
}

for name, model in models.items():
    model.fit(X_train_scaled, y_train)
    y_pred = model.predict(X_test_scaled)
    rmse   = np.sqrt(mean_squared_error(y_test, y_pred))
    print(f"{name} RMSE: {rmse:.4f}")

LinearRegression RMSE: 4.3310
Lasso RMSE: 6.9869
Ridge RMSE: 4.3171
ElasticNet RMSE: 7.3406


In [15]:
# (2) Standardization       : 표준화         : (X - Mean) / SD         : -3 ~ +3
scaler         = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled  = scaler.transform(X_test)

models = {
    "LinearRegression" : LinearRegression(),
    "Lasso"            : Lasso(),           
    "Ridge"            : Ridge(),           
    "ElasticNet"       : ElasticNet()  
}

for name, model in models.items():
    model.fit(X_train_scaled, y_train)
    y_pred = model.predict(X_test_scaled)
    rmse   = np.sqrt(mean_squared_error(y_test, y_pred))
    print(f"{name} RMSE: {rmse:.4f}")

LinearRegression RMSE: 4.3310
Lasso RMSE: 4.6755
Ridge RMSE: 4.3293
ElasticNet RMSE: 4.7776


### II. 분류(Classification)

In [16]:
# 데이터 읽어오기 : cancer.csv
file_path = "d:/KIPI/cancer.csv"
cancer    = pd.read_csv(file_path)
cancer.head()

id diagnosis  radius_mean  texture_mean  perimeter_mean  area_mean  \
0    842302         M        17.99         10.38          122.80     1001.0   
1    842517         M        20.57         17.77          132.90     1326.0   
2  84300903         M        19.69         21.25          130.00     1203.0   
3  84348301         M        11.42         20.38           77.58      386.1   
4  84358402         M        20.29         14.34          135.10     1297.0   

   smoothness_mean  compactness_mean  concavity_mean  concave points_mean  \
0          0.11840           0.27760          0.3001              0.14710   
1          0.08474           0.07864          0.0869              0.07017   
2          0.10960           0.15990          0.1974              0.12790   
3          0.14250           0.28390          0.2414              0.10520   
4          0.10030           0.13280          0.1980              0.10430   

   ...  radius_worst  texture_worst  perimeter_worst  area_worst  \
0  ...         25.38          17.33           184.60      2019.0   
1  ...         24.99          23.41           158.80      1956.0   
2  ...         23.57          25.53           152.50      1709.0   
3  ...         14.91          26.50            98.87       567.7   
4  ...         22.54          16.67           152.20      1575.0   

   smoothness_worst  compactness_worst  concavity_worst  concave points_worst  \
0            0.1622             0.6656           0.7119                0.2654   
1            0.1238             0.1866           0.2416                0.1860   
2            0.1444             0.4245           0.4504                0.2430   
3            0.2098             0.8663           0.6869                0.2575   
4            0.1374             0.2050           0.4000                0.1625   

   symmetry_worst  fractal_dimension_worst  
0          0.4601                  0.11890  
1          0.2750                  0.08902  
2          0.3613                  0.08758  
3          0.6638                  0.17300  
4          0.2364                  0.07678  

[5 rows x 32 columns]

In [17]:
# 데이터의 정보 보기
cancer.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 569 entries, 0 to 568
Data columns (total 32 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       569 non-null    int64  
 1   diagnosis                569 non-null    object 
 2   radius_mean              569 non-null    float64
 3   texture_mean             569 non-null    float64
 4   perimeter_mean           569 non-null    float64
 5   area_mean                569 non-null    float64
 6   smoothness_mean          569 non-null    float64
 7   compactness_mean         569 non-null    float64
 8   concavity_mean           569 non-null    float64
 9   concave points_mean      569 non-null    float64
 10  symmetry_mean            569 non-null    float64
 11  fractal_dimension_mean   569 non-null    float64
 12  radius_se                569 non-null    float64
 13  texture_se               569 non-null    float64
 14  perimeter_se             5

In [18]:
# 데이터 전처리 : (1) id 열 삭제하기
cancer = cancer.drop(columns = ["id"])
cancer.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 569 entries, 0 to 568
Data columns (total 31 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   diagnosis                569 non-null    object 
 1   radius_mean              569 non-null    float64
 2   texture_mean             569 non-null    float64
 3   perimeter_mean           569 non-null    float64
 4   area_mean                569 non-null    float64
 5   smoothness_mean          569 non-null    float64
 6   compactness_mean         569 non-null    float64
 7   concavity_mean           569 non-null    float64
 8   concave points_mean      569 non-null    float64
 9   symmetry_mean            569 non-null    float64
 10  fractal_dimension_mean   569 non-null    float64
 11  radius_se                569 non-null    float64
 12  texture_se               569 non-null    float64
 13  perimeter_se             569 non-null    float64
 14  area_se                  5

In [20]:
cancer['diagnosis'].value_counts(normalize = True)

diagnosis
B    0.627417
M    0.372583
Name: proportion, dtype: float64

In [21]:
# 데이터 전처리(2) : "B" -> 0, "M" -> 1
# y : dianogis : 0과 1로만 구성되어 있어야 함
# "B" : 양성(Benign)    : 0
# "M" : 악성(Malignant) : 1

cancer["diagnosis"] = cancer["diagnosis"].map({"B": 0, "M": 1})
cancer['diagnosis'].value_counts(normalize = True)

diagnosis
0    0.627417
1    0.372583
Name: proportion, dtype: float64

In [22]:
# 데이터 분할하기 : 훈련 데이터 70%, 평가 데이터 30%
# y : diagnosis
# X : y 이외의 모든 열

y = cancer["diagnosis"]
X = cancer.drop(columns = ["diagnosis"])

X_train, X_test, y_train, y_test = train_test_split(
    X, 
    y,
    test_size    = 0.3,
    random_state = 42,
    stratify     = y   # 층화추출
)

print("훈련 데이터 크기 :", X_train.shape, y_train.shape)
print("평가 데이터 크기 :", X_test.shape,  y_test.shape)
print("훈련 세트 내 타깃 분포 :\n", y_train.value_counts(normalize = True))
print("평가 세트 내 타깃 분포 :\n", y_test.value_counts(normalize = True))

훈련 데이터 크기 : (398, 30) (398,)
평가 데이터 크기 : (171, 30) (171,)
훈련 세트 내 타깃 분포 :
 diagnosis
0    0.628141
1    0.371859
Name: proportion, dtype: float64
평가 세트 내 타깃 분포 :
 diagnosis
0    0.625731
1    0.374269
Name: proportion, dtype: float64


In [29]:
# 분류 모형 : Logistic Regression, DT(Decition Tree), RF(Random Forest), XGBoost

# 1단계 : 분류 모형 구축(생성)
# 2단계 : 훈련(학습)
# 3단계 : 예측(분류)
# 4단계 : 평가(Recall, Precision, F1-Score, Accuracy) : 0 ~ 1

models = {
    "LogisticRegression" : LogisticRegression(random_state = 42, solver = 'liblinear'),
    "DecisionTree"       : DecisionTreeClassifier(random_state = 42),
    "RandomForest"       : RandomForestClassifier(random_state = 42),
    "XGBoost"            : XGBClassifier(random_state      = 42, 
                                         use_label_encoder = False, 
                                         eval_metric       = 'logloss')
}

for name, model in models.items():
    model.fit(X_train, y_train)
    y_pred    = model.predict(X_test)
    accuracy  = accuracy_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred)
    recall    = recall_score(y_test, y_pred)
    f1        = f1_score(y_test, y_pred)
    cm        = confusion_matrix(y_test, y_pred)

    print(f"=== {name} ===")
    print(f"Accuracy (정확도)  : {accuracy:.4f}")
    print(f"Precision (정밀도) : {precision:.4f}")
    print(f"Recall (재현율)    : {recall:.4f}")
    print(f"F1-score          : {f1:.4f}")
    
    # 혼동 행렬 출력
    print("Confusion Matrix:")
    print(cm)
    print("------------------------------")

=== LogisticRegression ===
Accuracy (정확도)  : 0.9474
Precision (정밀도) : 0.9825
Recall (재현율)    : 0.8750
F1-score          : 0.9256
Confusion Matrix:
[[106   1]
 [  8  56]]
------------------------------
=== DecisionTree ===
Accuracy (정확도)  : 0.9006
Precision (정밀도) : 0.8852
Recall (재현율)    : 0.8438
F1-score          : 0.8640
Confusion Matrix:
[[100   7]
 [ 10  54]]
------------------------------
=== RandomForest ===
Accuracy (정확도)  : 0.9649
Precision (정밀도) : 1.0000
Recall (재현율)    : 0.9062
F1-score          : 0.9508
Confusion Matrix:
[[107   0]
 [  6  58]]
------------------------------
=== XGBoost ===
Accuracy (정확도)  : 0.9766
Precision (정밀도) : 1.0000
Recall (재현율)    : 0.9375
F1-score          : 0.9677
Confusion Matrix:
[[107   0]
 [  4  60]]
------------------------------


C:\Users\LG\anaconda3\Lib\site-packages\xgboost\core.py:158: UserWarning: [14:15:39] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-08cbc0333d8d4aae1-1\xgboost\xgboost-ci-windows\src\learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
